# Durable Rules로 규칙 구현하기
- 산업인공지능학과 대학원
    2022254026
        김홍열

### Durable Rules 란?
* 비즈니스 룰 엔진을 구현하기 위한 라이브러리로 python, ruby, nodejs로 구현할 수 있다.

### Durable Rules 설치하기 (Python)
``` plantext
pip install durable_rules

### Durable Rules 다운로드
[github - jruizgit/rules](https://github.com/jruizgit/rules)

##### 패키지 불러오기

In [2]:
from durable.lang import *

#### 구현할 규칙
![2차전지 라인 구성도](./images/2ndBatteryLine.png)
> 규칙
``` plain
1. IF Input Left_JR AND Right_JR
		THEN Form JR
		
2. IF Form Left_JR AND Right_JR
		THEN Cut Left_JR AND Right_JR
		
3. IF Cut Left_JR AND Right_JR
		THEN Align Left_JR AND Right_JR
		
4. IF Pass Align Vision_Inspection
		THEN Return Result_None
		AND F&C&T

5. ELSE Align Vision_Inspection
		THEN Move Left Point
		AND Move Right Point

6. IF Move Left And Right Point
		THEN Align Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		AND F&C&T
		
7. IF Pass F&C&T Vision_Inspection
		THEN Return Result_None
		AND I&T

8. ELSE F&C&T Vision_Inspection
		THEN Front Vision_Inspection
		AND Rear Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG

9. IF Front AND Rear Vision_Inspection
		THEN Rotate JR

10. IF Rotate JR
		THEN Left Vision_Inspection
		AND Right Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		AND I&T

11. IF Pass I&T Vision_Inspection
		THEN Return Result_None
		AND C&W
		
12. ELSE I&T Vision_Inspection
		THEN Left Vision_Inspection
		AND Right Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		
13. IF Left AND Right Vision_Inspection
		THEN Move Up JR
		AND Rotate JR
		
14. IF Rotate JR
		THEN Front Vision_Inspection
		AND Rear Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		AND C&W
		
15. IF Pass C&W Vision_Inspection
		THEN Return None Result
		AND R&T
		
16. ELSE C&W Vision_Inspection
		THEN Left Vision_Inspection
		AND Right Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		AND R&T
		
17. IF Pass R&T Vision_Inspection
		THEN Return Result_None
		AND Wrapping
		
18. ELSE R&T Vision_Inspection
		THEN Left Vision_Inspection
		AND Right Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		AND Wrapping
		
19. IF Pass Wrapping Vision_Inspection
		THEN Return Result_None
		AND C&C&W
		
20. ELSE Wrapping Vision_Inspection
		THEN Front Vision_Inspection
		AND Rear Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		
21. IF Front AND Rear Vision_Inspection
		THEN Rotate JR
		
22. IF Rotate JR
		THEN Left Vision_Inspection
		AND Right Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG
		
23. IF Left AND Right Vision_Inspection
		THEN Retrun Result_OK
			OR Retrun Result_NG
		AND C&C&W
		
24. IF Pass C&C&W Vision_Inspection
		THEN Return Result_None
		
25. ELSE C&C&W Vision_Inspection
		THEN Long_Axis Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG

26. IF Long_Axis Vision_Inspection
		THEN Retrun Result_OK
			OR Retrun Result_NG
		AND Rotate JR

27. IF Rotate JR
		THEN Short_Axis Vision_Inspection
		AND Retrun Result_OK
			OR Retrun Result_NG

### 1. 각 라인 공정별 StateFlow 구현

In [1]:
from durable.lang import *

inspectionResult = ['OK','OK','OK','OK','OK','OK','OK'] #
def updateState(s, m):  # 
    s.JobID = m.JobID
    s.Pass = m.Pass
    s.Left = m.Left
    s.Right = m.Right
    s.Judge0 = m.Judge0
    s.Judge1 = m.Judge1
    s.Judge2 = m.Judge2
    s.Judge3 = m.Judge3
    s.Judge4 = m.Judge4
    s.Judge5 = m.Judge5
    s.Judge6 = m.Judge6


with flowchart('battery_assembley_process'):
    with stage('Input'):
        @run
        def nextToJR(c):
            print('>> current stage is Input')
            updateState(c.s, c.m)
            print ('Input JobID: {0}'.format(c.m.JobID))

        to('JR').when_all((m.JobID != None))
        to('Alarm').when_all((m.JobID == None))
        
            
    with stage('JR'):
        @run
        def nextToF_C(c):
            print('> current stage is JR')
            updateState(c.s, c.m) # JobID는 전달되나 나머지 파라미터들은 전달되지 않음
            print(c.s.Judge)
            if c.m.Left is None: # @when_all(m.Left != None) 조건으로 함수를 별도로도 생성해보았으나 인식 안 됨
                print('Alarm: Did not receive the Left JR.')
            if c.m.Right is None:
                print('Alarm: Did not receive the Right JR.')
            if c.m.Left is not None and c.m.Right is not None:
                print ('Both the Left JR[{0}] and the Right JR[{1}] have been assembled.'.format(c.m.Left, c.m.Right))
        
        to('Alarm').when_any((m.Left == None),
                            (m.Right == None))
        to('F&C')

    with stage('F&C'):
        @run
        def NextToAlign(c):
            print ('> current stage is F&C')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('F&C Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[0]}.')
            else:
                print('F&C Inspection is passed.')

        to('Align')

    with stage('Align'):
        @run
        def NextToI_T(c):
            print ('> current stage is Align')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('Align Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[1]}.')
            else:
                print('Align Inspection is passed.')

        to('I&T')

    with stage('I&T'):
        @run
        def NextToCAPWelding(c):
            print ('> current stage is I&T')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('I&T Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[2]}.')
            else:
                print('I&T Inspection is passed.')

        to('CAPWelding')

    with stage('CAPWelding'):
        @run
        def NextToRetainer(c):
            print ('> current stage is CAPWelding')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('CAPWelding Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[3]}.')
            else:
                print('CAPWelding Inspection is passed.')

        to('Retainer')

    with stage('Retainer'):
        @run
        def NextToWrapping(c):
            print ('> current stage is Retainer')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('Retainer Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[4]}.')
            else:
                print('Retainer Inspection is passed.')

        to('Wrapping')

    with stage('Wrapping'):
        @run
        def NextToC_CWelding(c):
            print ('> current stage is Wrapping')
            updateState(c.s, c.m)
            if c.m.Pass is False:
                print('Wrapping Inspection has been processed.')
                print(f'F&C Judgement: {inspectionResult[5]}.')
            else:
                print('Wrapping Inspection is passed.')

        to('C&CWelding')

    with stage('C&CWelding'):
        @run
        def InspectionComplete(c):
            print ('> current stage is C&CWelding')
            updateState(c.s, c.m)
            # c.s.JobID = c.m.JobID
            # c.s.Pass = c.m.Pass
            # c.s.Left = c.m.Left
            # c.s.Right = c.m.Right
            # c.s.Judge0 = c.m.Judge0
            # c.s.Judge1 = c.m.Judge1
            # c.s.Judge2 = c.m.Judge2
            # c.s.Judge3 = c.m.Judge3
            # c.s.Judge4 = c.m.Judge4
            # c.s.Judge5 = c.m.Judge5
            # c.s.Judge6 = c.m.Judge6
            if c.m.Pass is False:
                print('C&CWelding Inspection has been processed.')
                # inspectionResult[6] = 'TEST'
                # c.s.Judge6 = c.m.Judge6 = 'NG'
                print(f'F&C Judgement: {inspectionResult[6]}.')
            else:
                print('C&CWelding Inspection is passed.')

        to('Output')

    with stage('Output'):
        @run
        def InspectionComplete(c):
            print ('> current stage is Output')
            result = 'OK'
            for rst in inspectionResult:
                if rst == 'NG':
                    result = 'NG'
                    break
            # print(inspectionResult)
            # print (result)
            # print(c.s.JobID)
            # print(c.s.Judge)
            # print(c.s.Judge6)
            print ('JobID[{0}]\'s Result is {1}'.format(c.s.JobID, result))

    with stage('Alarm'):
        @run
        def Log(c):
            print ('The process will not proceed due to an alarm being triggered. - [JobID: ' +  str(c.m.JobID) + ']')

### 2. Input Data 구현

In [2]:
# 만들어진 규칙에 넣을 데이터들, 라인에 들어가는 각 배터리의 정보
post('battery_assembley_process', { 'JobID': None,
                                    'Pass': False,
                                    'Left': 100,
                                    'Right': 100,
                                    # 'Judge0': None,
                                    # 'Judge1': None,
                                    # 'Judge2': None,
                                    # 'Judge3': None,
                                    # 'Judge4': None,
                                    # 'Judge5': None,
                                    # 'Judge6': None})
                                    'Judge':[None, None, None, None, None, None, None]})
post('battery_assembley_process', { 'sid': 1,
                                    'JobID': '20230417', 
                                    'Pass': False,
                                    'Left': 100,
                                    'Right': None,
                                    # 'Judge0': None,
                                    # 'Judge1': None,
                                    # 'Judge2': None,
                                    # 'Judge3': None,
                                    # 'Judge4': None,
                                    # 'Judge5': None,
                                    # 'Judge6': None})
                                    'Judge':[None, None, None, None, None, None, None]})
post('battery_assembley_process', { 'sid': 2,
                                    'JobID': '20230418', 
                                    'Pass': False,
                                    'Left': None,
                                    'Right': 100,
                                    # 'Judge0': None,
                                    # 'Judge1': None,
                                    # 'Judge2': None,
                                    # 'Judge3': None,
                                    # 'Judge4': None,
                                    # 'Judge5': None,
                                    # 'Judge6': None})
                                    'Judge':[None, None, None, None, None, None, None]})

inspectionResult = ['OK','OK','OK','OK','NG','OK','OK'] # 내부적으로 Judege를 접근해서 변경할 수 없어서 테스트용으로 생성함
post('battery_assembley_process', { 'sid': 3,
                                    'JobID': '20230419', 
                                    'Pass': False,
                                    'Left': 100,
                                    'Right': 100,
                                    'Judge0': None,
                                    'Judge1': None,
                                    'Judge2': None,
                                    'Judge3': None,
                                    'Judge4': None,
                                    'Judge5': None,
                                    'Judge6': 'OK'})
                                    # 'Judge':[None, None, None, None, None, None, None]}) # Array를 제공하는듯 보이지만 allitems 같은 불편함을 감수해야됨


>> current stage is Input
The process will not proceed due to an alarm being triggered. - [JobID: None]
>> current stage is Input
> current stage is JR
> current stage is F&C
> current stage is Align
> current stage is I&T
> current stage is CAPWelding
> current stage is Retainer
> current stage is Wrapping
> current stage is C&CWelding
> current stage is Output
JobID[20230417]'s Result is OK
>> current stage is Input
> current stage is JR
> current stage is F&C
> current stage is Align
> current stage is I&T
> current stage is CAPWelding
> current stage is Retainer
> current stage is Wrapping
> current stage is C&CWelding
> current stage is Output
JobID[20230418]'s Result is OK
>> current stage is Input
> current stage is JR
> current stage is F&C
> current stage is Align
> current stage is I&T
> current stage is CAPWelding
> current stage is Retainer
> current stage is Wrapping
> current stage is C&CWelding
> current stage is Output
JobID[20230419]'s Result is NG


{'sid': '3',
 'id': 'sid-3',
 '$s': 1,
 'running': True,
 'exception': 'exception caught \'NoneType\' object has no attribute \'JobID\', traceback [\'  File "/config/.local/lib/python3.10/site-packages/durable/engine.py", line 241, in run\\n    self._func(c)\\n\', \'  File "/tmp/ipykernel_31962/4233634066.py", line 129, in InspectionComplete\\n    updateState(c.s, c.m)\\n\', \'  File "/tmp/ipykernel_31962/4233634066.py", line 5, in updateState\\n    s.JobID = m.JobID\\n\']',
 'JobID': '20230419',
 'Pass': False,
 'Left': 100,
 'Right': 100}

### 결과
* Durable_rule에서 사용되는 규칙을 별도로 습득 해야됨
* 내부적으로 메모리에 저장되는 것들을 접근하거나 디버깅할 수 없음
* 위 코드는 flowchart를 사용하였지만, statechart나 ruleset을 사용하여도 post를 상태마다 날려야 됨
* 내부적으로 어떻게 병렬처리 되는지 커스터마이징 할 수 없음
* 실무에 적용하기에 라이센스나 개발환경에 제약이 많음
* 상태패턴을 구현해서 직접 제어하는 것이 훨씬 효율적으로 보임